In [1]:
import whisper
print(whisper.__file__)


/home/tesla/miniconda3/envs/DUY/lib/python3.9/site-packages/whisper/__init__.py


In [1]:
import os

os.environ["CUDA_VISIBLE_DEVICES"] = "0"

In [3]:
import torch

print(torch.cuda.is_available())


print(torch.cuda.device_count())


print(torch.cuda.current_device())
print(torch.cuda.device(0))

print(torch.cuda.get_device_name(0))


True
2
0
Tesla T4


In [2]:
from huggingface_hub import notebook_login

notebook_login()

In [2]:
model_name_or_path = "openai/whisper-medium"
task = "transcribe"

In [3]:
dataset_name = "Vin100h_MITI_private"
language = "Vietnamese"
language_abbr = "vi" # Short hand code for the language we want to fine-tune

In [4]:
    # Load Dataset
from datasets import load_dataset, DatasetDict, load_from_disk
processed_dataset = DatasetDict()
processed_dataset = load_from_disk("./MITI_clean")
processed_dataset2 = load_from_disk("./vin_10h/")

print(processed_dataset)
print(processed_dataset2)

DatasetDict({
    train: Dataset({
        features: ['input_features', 'input_length', 'attention_mask', 'labels'],
        num_rows: 1679
    })
    test: Dataset({
        features: ['input_features', 'input_length', 'attention_mask', 'labels'],
        num_rows: 420
    })
})
DatasetDict({
    train: Dataset({
        features: ['input_features', 'input_length', 'attention_mask', 'labels'],
        num_rows: 6735
    })
    test: Dataset({
        features: ['input_features', 'input_length', 'attention_mask', 'labels'],
        num_rows: 1688
    })
})


In [49]:
from datasets import Dataset

# Assuming you have already loaded your dataset
# processed_dataset2 = ...

# Randomly select 5000 indices from the train dataset
import random
num_samples_train = 5000
num_samples_test = 600
random_indices_train = random.sample(range(len(processed_dataset2['train'])), num_samples_train)
random_indices_test = random.sample(range(len(processed_dataset2['test'])), num_samples_test)

# Initialize lists for train dataset
input_features_train = []
input_length_train = []
attention_mask_train = []
labels_train = []

# Initialize lists for test dataset
input_features_test = []
input_length_test = []
attention_mask_test = []
labels_test = []

# Populate lists for train dataset
for i in random_indices_train:
    input_features_train.append(processed_dataset2['train'][i]['input_features'])
    input_length_train.append(processed_dataset2['train'][i]['input_length'])
    attention_mask_train.append(processed_dataset2['train'][i]['attention_mask'])
    labels_train.append(processed_dataset2['train'][i]['labels'])

# Populate lists for test dataset
for i in random_indices_test:
    input_features_test.append(processed_dataset2['test'][i]['input_features'])
    input_length_test.append(processed_dataset2['test'][i]['input_length'])
    attention_mask_test.append(processed_dataset2['test'][i]['attention_mask'])
    labels_test.append(processed_dataset2['test'][i]['labels'])

# Create a new dataset with the randomly selected rows
random_subset = Dataset.from_dict({
    'train': {
        'input_features': input_features_train,
        'input_length': input_length_train,
        'attention_mask': attention_mask_train,
        'labels': labels_train,
    },
    'test': {
        'input_features': input_features_test,
        'input_length': input_length_test,
        'attention_mask': attention_mask_test,
        'labels': labels_test,
    }
})




In [5]:
import datasets
concat = DatasetDict()
concat["train"] = datasets.concatenate_datasets([processed_dataset["train"], processed_dataset2["train"]])
concat['test']= datasets.concatenate_datasets([processed_dataset["test"], processed_dataset2["test"]])


In [7]:
concat

DatasetDict({
    train: Dataset({
        features: ['input_features', 'input_length', 'attention_mask', 'labels'],
        num_rows: 8414
    })
    test: Dataset({
        features: ['input_features', 'input_length', 'attention_mask', 'labels'],
        num_rows: 2108
    })
})

In [7]:
from transformers import WhisperFeatureExtractor

feature_extractor = WhisperFeatureExtractor.from_pretrained(model_name_or_path)

In [6]:

from transformers import WhisperTokenizer

tokenizer = WhisperTokenizer.from_pretrained(model_name_or_path, language=language, task=task)

In [11]:
tokenizer.save_pretrained('./Viet_ASR')

('./Viet_ASR/tokenizer_config.json',
 './Viet_ASR/special_tokens_map.json',
 './Viet_ASR/vocab.json',
 './Viet_ASR/merges.txt',
 './Viet_ASR/normalizer.json',
 './Viet_ASR/added_tokens.json')

In [8]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union
from transformers import WhisperProcessor

processor = WhisperProcessor.from_pretrained(model_name_or_path, language=language, task=task)
@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]


        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")

         # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.processor.tokenizer.bos_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch
data_collator = DataCollatorSpeechSeq2SeqWithPadding(processor=processor)

In [9]:
import evaluate

metric = evaluate.load("wer")

In [12]:
from transformers import WhisperForConditionalGeneration

model = WhisperForConditionalGeneration.from_pretrained('openai/whisper-medium', load_in_8bit=True, device_map="auto" )

In [13]:
model.config.forced_decoder_ids = None
model.config.suppress_tokens = []

In [14]:
from peft import prepare_model_for_kbit_training

model = prepare_model_for_kbit_training(model)
def make_inputs_require_grad(module, input, output):
    output.requires_grad_(True)

model.model.encoder.conv1.register_forward_hook(make_inputs_require_grad)

In [15]:
from peft import LoraConfig, PeftModel, LoraModel, LoraConfig, get_peft_model
#target_modules = ["k_proj", "q_proj", "v_proj", "out_proj", "fc1", "fc2"] #will it better ?
target_modules=["q_proj", "v_proj"]
config = LoraConfig(r=32, lora_alpha=64, target_modules=target_modules, lora_dropout=0.05, bias="none")

model = get_peft_model(model, config)
model.print_trainable_parameters()

trainable params: 9,437,184 || all params: 773,295,104 || trainable%: 1.2203858463844612


In [16]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="./Vietnamese_ASR", 
    per_device_train_batch_size=10,
    #auto_find_batch_size  = True,
    gradient_accumulation_steps=2,  # increase by 2x for every 2x decrease in batch size
    learning_rate=5e-5,
    warmup_steps=50,
    num_train_epochs=3,
    evaluation_strategy="epoch",
    gradient_checkpointing=True,
    optim="adamw_torch",
    fp16=True,
    per_device_eval_batch_size=8,
    generation_max_length=225,
    logging_steps=100,
    report_to=["tensorboard"],
    predict_with_generate=True,
    # load_best_model_at_end=True,
    greater_is_better=False,
    save_strategy = "epoch",
    # required as the PeftModel forward doesn't have the signature of the wrapped model's forward
    remove_unused_columns=False,
    label_names=["labels"],  # same reason as above
    push_to_hub=True,
)

In [19]:
from transformers import Seq2SeqTrainer, TrainerCallback, TrainingArguments, TrainerState, TrainerControl
from transformers.trainer_utils import PREFIX_CHECKPOINT_DIR


class SavePeftModelCallback(TrainerCallback):
    def on_save(
        self,
        args: TrainingArguments,
        state: TrainerState,
        control: TrainerControl,
        **kwargs,
    ):
        checkpoint_folder = os.path.join(args.output_dir, f"{PREFIX_CHECKPOINT_DIR}-{state.global_step}")

        peft_model_path = os.path.join(checkpoint_folder, "adapter_model")
        kwargs["model"].save_pretrained(peft_model_path)

        pytorch_model_path = os.path.join(checkpoint_folder, "pytorch_model.bin")
        if os.path.exists(pytorch_model_path):
            os.remove(pytorch_model_path)
        return control


trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=concat["train"],
    eval_dataset=concat["test"],
    data_collator=data_collator,
    # compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor,
    callbacks=[SavePeftModelCallback],
)
model.config.use_cache = False  # silence the warnings. Please re-enable for inference!

/media/tesla/New Volume/DEMO/DUY/Vietnamese_ASR/./Vietnamese_ASR is already a clone of https://huggingface.co/DuyTa/Vietnamese_ASR. Make sure you pull the latest changes with `repo.git_pull()`.


In [20]:
trainer.train()

  0%|          | 0/1263 [00:00<?, ?it/s]

/home/tesla/miniconda3/envs/DUY/lib/python3.9/site-packages/bitsandbytes/autograd/_functions.py:322: UserWarning: MatMul8bitLt: inputs will be cast from torch.float32 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")


{'loss': 1.9814, 'learning_rate': 4.814509480626546e-05, 'epoch': 0.24}
{'loss': 0.6861, 'learning_rate': 4.402308326463314e-05, 'epoch': 0.48}
{'loss': 0.3736, 'learning_rate': 3.9901071723000826e-05, 'epoch': 0.71}
{'loss': 0.332, 'learning_rate': 3.577906018136851e-05, 'epoch': 0.95}


  0%|          | 0/264 [00:00<?, ?it/s]

{'eval_loss': 0.3133259117603302, 'eval_runtime': 887.0949, 'eval_samples_per_second': 2.376, 'eval_steps_per_second': 0.298, 'epoch': 1.0}


...

/home/tesla/miniconda3/envs/DUY/lib/python3.9/site-packages/bitsandbytes/autograd/_functions.py:322: UserWarning: MatMul8bitLt: inputs will be cast from torch.float32 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")


{'loss': 0.2857, 'learning_rate': 1.5169002473206925e-05, 'epoch': 2.14}
{'loss': 0.2643, 'learning_rate': 1.104699093157461e-05, 'epoch': 2.38}
{'loss': 0.2604, 'learning_rate': 6.924979389942292e-06, 'epoch': 2.61}
{'loss': 0.2505, 'learning_rate': 2.8029678483099755e-06, 'epoch': 2.85}


  0%|          | 0/264 [00:00<?, ?it/s]

{'eval_loss': 0.27759623527526855, 'eval_runtime': 879.7333, 'eval_samples_per_second': 2.396, 'eval_steps_per_second': 0.3, 'epoch': 3.0}
{'train_runtime': 35575.7347, 'train_samples_per_second': 0.71, 'train_steps_per_second': 0.036, 'train_loss': 0.4555940831925127, 'epoch': 3.0}


TrainOutput(global_step=1263, training_loss=0.4555940831925127, metrics={'train_runtime': 35575.7347, 'train_samples_per_second': 0.71, 'train_steps_per_second': 0.036, 'train_loss': 0.4555940831925127, 'epoch': 3.0})

In [22]:
peft_model_id = "DuyTa/Vietnamese_ASR"
model.push_to_hub(peft_model_id)
print(peft_model_id)

DuyTa/Vietnamese_ASR


In [10]:
from peft import PeftModel, PeftConfig
from transformers import WhisperForConditionalGeneration
peft_model_id = "./Vietnamese_ASR"
peft_config = PeftConfig.from_pretrained(peft_model_id)
model = WhisperForConditionalGeneration.from_pretrained(
    peft_config.base_model_name_or_path, load_in_8bit=True, device_map="auto"
)
model = PeftModel.from_pretrained(model, peft_model_id)

In [11]:
from torch.utils.data import DataLoader
from tqdm import tqdm
import numpy as np
import gc

eval_dataloader = DataLoader(concat["test"], batch_size=24, collate_fn=data_collator)

model.eval()
for step, batch in enumerate(tqdm(eval_dataloader)):
    with torch.cuda.amp.autocast():
        with torch.no_grad():
            generated_tokens = (
                model.generate(
                    input_features=batch["input_features"].to("cuda"),
                    decoder_input_ids=batch["labels"][:, :4].to("cuda"),
                    max_new_tokens=255,
                )
                .cpu()
                .numpy()
            )
            labels = batch["labels"].cpu().numpy()
            labels = np.where(labels != -100, labels, tokenizer.pad_token_id)
            decoded_preds = tokenizer.batch_decode(generated_tokens, skip_special_tokens=True)
            decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)
            metric.add_batch(
                predictions=decoded_preds,
                references=decoded_labels,
            )
    del generated_tokens, labels, batch
    gc.collect()
wer = 100 * metric.compute()
print(f"{wer=}")

  0%|          | 0/88 [00:00<?, ?it/s]

/home/tesla/miniconda3/envs/DUY/lib/python3.9/site-packages/bitsandbytes/autograd/_functions.py:322: UserWarning: MatMul8bitLt: inputs will be cast from torch.float32 to float16 during quantization
  warnings.warn(f"MatMul8bitLt: inputs will be cast from {A.dtype} to float16 during quantization")
100%|██████████| 88/88 [59:07<00:00, 40.31s/it]

wer=15.57082617523036


## Text Norm

In [ ]:
# using Vietnamese text normalization after take whisper out token

In [12]:
from torch.utils.data import DataLoader
from tqdm import tqdm
import numpy as np
import gc
from transformers.models.whisper.english_normalizer import BasicTextNormalizer
normalizer = BasicTextNormalizer()
forced_decoder_ids = processor.get_decoder_prompt_ids(language=language, task=task)

model.eval()
for step, batch in enumerate(tqdm(eval_dataloader)):
    with torch.cuda.amp.autocast():
        with torch.no_grad():
            generated_tokens= model.generate(input_features=batch["input_features"].to("cuda"),
                                             forced_decoder_ids=forced_decoder_ids,
                                             max_new_tokens=255).cpu().numpy()
            labels = batch["labels"].cpu().numpy()
            labels = np.where(labels != -100, labels, processor.tokenizer.pad_token_id)
            decoded_preds = processor.tokenizer.batch_decode(generated_tokens, skip_special_tokens=True)
            decoded_labels = processor.tokenizer.batch_decode(labels, skip_special_tokens=True)
            metric.add_batch(
                predictions=[normalizer(pred).strip() for pred in decoded_preds],
                references=[normalizer(label).strip() for label in decoded_labels],
            )
    # if step==0:
    #     break
    del generated_tokens, labels, batch
    gc.collect()
normalized_wer = 100 * metric.compute()
print(f"{normalized_wer=}")

100%|██████████| 88/88 [58:18<00:00, 39.75s/it]

normalized_wer=14.601364195460137


In [13]:
for pred,label in zip(decoded_preds,decoded_labels):
  print(f"{pred=}, {label=}")

pred='toàn bộ phi hành đoàn đã bị giết chết khiến con tàu quân sự đậm thẳng vào ishimura', label='toàn bộ phi hành đoàn đã bị giết chết khiến con tàu quân sự đâm thẳng vào ishimura'
pred='đủ kinh nghiệm để mình quản lý nhân viên và mình làm sao để mình đưa ra một cái dịch vụ tốt nhất', label='đủ kinh nghiệm để mình quản lý nhân viên và mình làm sao để mình đưa ra một cái dịch vụ tốt nhất'
pred='nói một trong một cái chương trình trong tương lai về ngành thu y thì ở mỹ tất cả các đại học nào lớn đều có ngành thu y hết', label='<unk> nói một trong một cái chương trình trong tương lai về ngành thú y thì ở mỹ tất cả các đại học nào lớn đều có ngành thú y hết'
pred='phấn đấu đến năm hai ngàn không trăm hai mười có từ tám trăm đến một ngàn kinh nghiệp tham gia sàn sâu dịch thu mại điện tử của bộ công thương và quốc tế năm mươi phần trăm số này vô bắn trên sàn', label='phấn đấu đến năm hai ngàn không trăm hai mươi có từ tám trăm đến một ngàn doanh nghiệp tham gia sàn giao dịch thương mại điện

In [14]:
import torch
from transformers import (
    AutomaticSpeechRecognitionPipeline,
    WhisperForConditionalGeneration,
    WhisperTokenizer,
    WhisperProcessor,
)
from peft import PeftModel, PeftConfig


peft_model_id = "./Vietnamese_ASR"
language = "Vietnamese"
task = "transcribe"

peft_config = PeftConfig.from_pretrained(peft_model_id)
model = WhisperForConditionalGeneration.from_pretrained(
    peft_config.base_model_name_or_path
)
model = PeftModel.from_pretrained(model, peft_model_id)
merged_model = model.merge_and_unload()


In [16]:
merged_model.save_pretrained("./Vietnamese_ASR/merged")

In [17]:
from transformers import WhisperTokenizer

tokenizer = WhisperTokenizer.from_pretrained('openai/whisper-medium', language=language, task=task)

In [18]:
tokenizer.save_pretrained('./Vietnamese_ASR/merged')

('./Vietnamese_ASR/merged/tokenizer_config.json',
 './Vietnamese_ASR/merged/special_tokens_map.json',
 './Vietnamese_ASR/merged/vocab.json',
 './Vietnamese_ASR/merged/merges.txt',
 './Vietnamese_ASR/merged/normalizer.json',
 './Vietnamese_ASR/merged/added_tokens.json')

In [19]:
!ct2-transformers-converter --model ./Vietnamese_ASR/merged --output_dir ./Vietnamese_ASR/ct2ranslate

/bin/bash: /home/tesla/miniconda3/lib/libtinfo.so.6: no version information available (required by /bin/bash)


In [20]:
!ct2-transformers-converter --model ./Vietnamese_ASR/merged --output_dir ./Vietnamese_ASR/ct2ranslate/quantized --quantization float16

/bin/bash: /home/tesla/miniconda3/lib/libtinfo.so.6: no version information available (required by /bin/bash)


In [6]:
from huggingface_hub import Repository
repo = Repository(local_dir="", clone_from='DuyTa/Vietnamese_ASR')

/media/tesla/New Volume/DEMO/DUY/Vietnamese_ASR/Vietnamese_ASR/src/Vietnamese_ASR is already a clone of https://huggingface.co/DuyTa/Vietnamese_ASR. Make sure you pull the latest changes with `repo.git_pull()`.


In [6]:
repo.git_pull(rebase=True)

Clean file runs/Aug17_22-42-43_tesla-T4/events.out.tfevents.1692289257.tesla-T4.201346.0:  14%|#4        | 1.0…

In [ ]:
repo.git_add(".")
repo.git_commit(commit_message="3 epochs finetuning and quantized model )")

In [8]:
repo.git_push()

Several commits (3) will be pushed upstream.
The progress bars may be unreliable.


To https://huggingface.co/DuyTa/Vietnamese_ASR
   63bacc4..82e8e84  main -> main



'https://huggingface.co/DuyTa/Vietnamese_ASR/commit/82e8e84fe4f1ffee17eff82c39a163f4b81335d5'

In [ ]:
merged_model.push_to_hub("DuyTa/MITI_Whisper")

In [ ]:
import torch
import gradio as gr
from transformers import (
    AutomaticSpeechRecognitionPipeline,
    WhisperForConditionalGeneration,
    WhisperTokenizer,
    WhisperProcessor,
)
from peft import PeftModel, PeftConfig


peft_model_id = "DuyTa/MITI_Whisper"
language = "Vietnamese"
task = "transcribe"
peft_config = PeftConfig.from_pretrained(peft_model_id)
model = WhisperForConditionalGeneration.from_pretrained(
    peft_config.base_model_name_or_path, load_in_8bit=True, device_map="auto"
)

model = PeftModel.from_pretrained(model, peft_model_id)
tokenizer = WhisperTokenizer.from_pretrained(peft_config.base_model_name_or_path, language=language, task=task)
processor = WhisperProcessor.from_pretrained(peft_config.base_model_name_or_path, language=language, task=task)
feature_extractor = processor.feature_extractor
forced_decoder_ids = processor.get_decoder_prompt_ids(language=language, task=task)
pipe = AutomaticSpeechRecognitionPipeline(model=model, tokenizer=tokenizer, feature_extractor=feature_extractor)


def transcribe(audio):
    with torch.cuda.amp.autocast():
        text = pipe(audio, generate_kwargs={"forced_decoder_ids": forced_decoder_ids}, max_new_tokens=255)["text"]
    return text


iface = gr.Interface(
    fn=transcribe,
    inputs=gr.Audio(source="upload", type="filepath"),
    outputs="text",
    title="PEFT LoRA",
    description="Realtime demo for Vietnamese speech recognition using `PEFT-LoRA+INT8` fine-tuned Whisper Medium .",
)

iface.launch(share=True)